In [2]:
import os
import sys
import re
import time
import wave
import hashlib
from uuid import uuid4
from datetime import datetime

import numpy as np
import pygame
import pdfplumber
# import pytesseract
# import soundfile as sf
from scipy.io import wavfile
from IPython.display import display, Audio
from reportlab.platypus import SimpleDocTemplate, Paragraph, Spacer
from reportlab.lib.styles import getSampleStyleSheet
from reportlab.lib.pagesizes import A4

from pinecone import Pinecone, ServerlessSpec
from langchain import hub
from langchain.schema import Document
from langchain.text_splitter import CharacterTextSplitter
from langchain.chains import create_retrieval_chain
from langchain.chains.question_answering import load_qa_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_pinecone import PineconeVectorStore
from langchain_google_genai import GoogleGenerativeAIEmbeddings, ChatGoogleGenerativeAI
import google.generativeai as genai
import numpy as np
from kokoro import KPipeline
from moviepy.editor import (
    VideoFileClip,
    AudioFileClip,
    TextClip,
    CompositeVideoClip,
    ColorClip,
)
from moviepy.config import change_settings

In [3]:
sys.path.append("../my_apis")
import apis

In [4]:
import sys
print(sys.executable)


c:\Users\user\Desktop\myproai\my_proai\Scripts\python.exe


In [46]:
pinecone_api_key = apis.pinecone_Api_vector_db
gemini_api_key = apis.gemini_key
Index_name = "myproaiassistant"
# file_path = r"../my_documents/(Book)Linear Algebra and its Application.pdf"
file_path = r"../my_documents/pp_week1.pdf"
os.environ["GOOGLE_API_KEY"] = apis.gemini_key
os.environ["PINECONE_API_KEY"] = apis.pinecone_Api_vector_db
gemini_model_for_embaddings = "models/embedding-001"
gemini_model_for_query = "gemini-2.5-pro"
audio_clip = r"../my_audios/123456.wav"
# ImageMagick  path
change_settings(
    {"IMAGEMAGICK_BINARY": r"C:\Program Files\ImageMagick-7.1.2-Q16-HDRI\magick.exe"}
)
unique_id = uuid4()
print(file_path)

../my_documents/pp_week1.pdf


In [7]:
# === Step 1: Extract text from PDF ===
def Extract_ext_from_PDF(file_path):
    pdf_text = ""

    with pdfplumber.open(file_path) as pdf:
        for page in pdf.pages:
            pdf_text += page.extract_text() + "\n"

    return pdf_text


pdf_text = Extract_ext_from_PDF(file_path)

In [8]:
# === Step 2: Create chunker with overlap ===


def chunk_and_overlap(c_size, c_overlap):
    text_splitter = CharacterTextSplitter(
        separator="\n",  # split by newlines
        chunk_size=c_size,  # max characters per chunk
        chunk_overlap=c_overlap,  # overlap between chunks
        length_function=len,
    )

    chunks = text_splitter.split_text(pdf_text)

    # === Step 3: Show result ===
    for i, chunk in enumerate(chunks, start=1):  # first 5 chunks
        print(f"--- Chunk {i} ---")
        print(chunk)
        print()
    return chunks

chunks = chunk_and_overlap(700, 100)

--- Chunk 1 ---
Ms. Kainat Anjum(kainat@biit.edu.pk) Professional Ethics Whatsapp # 03215023609
(SSH 307)
Page number 1
Text book & References:
Engineering Ethics by Charles B. Fleddermann (Fourth edition)
Managing Business Ethics, Straight Talk About How To Do It Right by Linda K. Trevino&
Katherine A. Nelson
Lesson 01-02
OBJECTIVES:
• To introduce “ethics” and “professional ethics”
• To let students know about certain key concepts in professional Practices/Ethics • To
understand code of conduct in professional set up
LIST OF TOPICS TO BE COVERED:
1. Key Concepts in Professional Ethics
2. The Importance of Ethical Conduct in Business
3. Code of Ethics

--- Chunk 2 ---
2. The Importance of Ethical Conduct in Business
3. Code of Ethics
Ms. Kainat Anjum(kainat@biit.edu.pk) Professional Ethics Whatsapp # 03215023609
(SSH 307)
Page number 2
Ethics:
“A branch of philosophy concerned with that which is deemed acceptable in human
behaviour, with what is good or bad, right or wrong in human co

In [9]:
def generating_embeddings(my_model, my_pc_Api):

    embeddings = GoogleGenerativeAIEmbeddings(
        model=my_model, pinecone_api_key=my_pc_Api
    )
    return embeddings


embeddings = generating_embeddings(
    gemini_model_for_embaddings, os.environ["PINECONE_API_KEY"]
)

In [10]:
# Creating index

def creating_Index(my_pc, my_IN):

    pc = my_pc

    cloud = "aws"
    region = "us-east-1"
    spec = ServerlessSpec(cloud=cloud, region=region)

    index_name = my_IN

    if index_name not in pc.list_indexes().names():
        pc.create_index(
            name=index_name, dimension=embeddings.dimension, metric="cosine", spec=spec
        )

    # See that it is empty
    print("Index before upsert:")
    print(pc.Index(index_name).describe_index_stats())
    print("\n")
    return pc


pc = creating_Index(Pinecone(os.environ["PINECONE_API_KEY"]), Index_name)

Index before upsert:
{'dimension': 768,
 'index_fullness': 0.0,
 'metric': 'cosine',
 'namespaces': {'myproaivectors': {'vector_count': 18}},
 'total_vector_count': 18,
 'vector_type': 'dense'}




In [11]:
# Embed and upsert each chunk as a distinct record in a namespace called myproaiNamespace


def distinct_record(my_ns, my_IN):

    documents = [Document(page_content=chunk) for chunk in chunks]

    # Assign unique but repeatable IDs (hash from text)
    ids = [hashlib.md5(doc.page_content.encode()).hexdigest() for doc in documents]

    docsearch = PineconeVectorStore.from_documents(
        documents=documents,
        index_name=my_IN,
        embedding=embeddings,
        namespace=my_ns,
        ids=ids,
    )

    time.sleep(5)

    # See how many vectors have been upserted
    print("Index after upsert:")
    print(pc.Index(Index_name).describe_index_stats())
    print("\n")
    time.sleep(2)
    return docsearch


docsearch = distinct_record("myproaivectors", Index_name)

Index after upsert:
{'dimension': 768,
 'index_fullness': 0.0,
 'metric': 'cosine',
 'namespaces': {'myproaivectors': {'vector_count': 18}},
 'total_vector_count': 18,
 'vector_type': 'dense'}




In [13]:
def checking_records(my_IN, my_ns):

    index = pc.Index(my_IN)

    for ids in index.list(namespace=my_ns):
        query = index.query(
            id=ids[0],
            namespace=my_ns,
            top_k=1,
            include_values=True,
            include_metadata=True,
        )
        print(query)
        print("\n")


checking_records(Index_name, "myproaivectors")

{'matches': [{'id': '13646d9595edd371e63289210e28c6c9',
              'metadata': {'text': 'e.g. Medical and Dental Council, Police '
                                   'Service Code of Conduct, Estate Agents '
                                   'Code\n'
                                   'Ms. Kainat Anjum(kainat@biit.edu.pk) '
                                   'Professional Ethics Whatsapp # '
                                   '03215023609\n'
                                   '(SSH 307)\n'
                                   'Page number 7\n'
                                   'of Conduct. Codes may not be exhaustive '
                                   'and may not include all the rules and\n'
                                   'regulations that apply to every situation. '
                                   'The contents therefore have to be viewed '
                                   'within\n'
                                   'the framework of company policies, '
              

In [14]:
def save_to_simple_pdf(question, answer, filename="query_result.pdf"):
    """Simple PDF export using reportlab"""
    doc = SimpleDocTemplate(filename, pagesize=A4)
    styles = getSampleStyleSheet()
    story = []

    # Add question
    # story.append(Paragraph(f"<b><font size='16'>Question:</font></b>", styles['Heading1']))
    # # story.append(Paragraph(question, styles['Normal']))
    # story.append(Spacer(1, 20))

    # Add answer
    # story.append(Paragraph(f"<b><font size='16'>Answer:</font></b>", styles['Heading1']))

    # Format the answer (handle line breaks)
    formatted_answer = answer.replace("\n", "<br/>")
    story.append(Paragraph(formatted_answer, styles["Normal"]))
    story.append(Spacer(1, 20))

    # Add timestamp
    story.append(
        Paragraph(
            f"<i>Generated on: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}</i>",
            styles["Italic"],
        )
    )

    doc.build(story)
    print(f" PDF saved: {filename}")

In [41]:
def relevant_knowledge(my_g_api_k, my_ns, my_k, my_g_qmodel, task_instruction):

    # ✅ Load retrieval QA prompt from LangChain Hub
    retrieval_qa_chat_prompt = hub.pull("langchain-ai/retrieval-qa-chat")

    # ✅ Create a retriever from your Pinecone vectorstore
    retriever = docsearch.as_retriever(search_kwargs={"namespace": my_ns, "k": my_k})

    # ✅ Gemini model for retrieval step
    llm_for_retrieval = ChatGoogleGenerativeAI(
        model=my_g_qmodel, temperature=0.0, google_api_key=my_g_api_k
    )

    # ✅ Combine docs chain
    combine_docs_chain = create_stuff_documents_chain(
        llm_for_retrieval, retrieval_qa_chat_prompt
    )

    # ✅ Retrieval chain
    retrieval_chain = create_retrieval_chain(retriever, combine_docs_chain)

    # 🔹 Step 1: Get context from vectorstore
    retrieval_result = retrieval_chain.invoke({"input": task_instruction})
    context = retrieval_result["answer"]

    # 🔹 Step 2: One message with system + user prompt
    messages = [
        (
            "system",
            "You are a helpful assistant that helps professors with tasks like making quizzes, assignments, or summaries. **Strictly use only the retrieved content and do not extract contact information related to Ms. Kainat Anjum**, provide all the headings please",
        ),
        (
            "user",
            f"Based only on the following content:\n\n{retrieval_result}\n\nTask: {task_instruction}",
        ),
    ]

    # ✅ Step 3: Final LLM call
    llm_for_task = ChatGoogleGenerativeAI(
        model=my_g_qmodel, temperature=0.0, google_api_key=my_g_api_k
    )

    final_result = llm_for_task.invoke(messages)
    print(final_result.content)

    # Save data to pdf

    my_file = input("Enter the name of your file: ")
    save_to_simple_pdf(
        task_instruction, final_result.content, f"../my_pdf_files/{my_file}.pdf"
    )

    return final_result, my_file


final_result, my_file = relevant_knowledge(
    gemini_api_key,
    "myproaivectors",
    18,
    gemini_model_for_query,
    "extract the text from page number 3 of given pdf. first find the the topic name from the overall pdf suitable to the asked content and provide it ''dont write topic name just directly provide me the topic. then, Separate the text and headings, do not include key concept word as a heading. make sure to extract each headings and text in a list format provide headings and text separately. do not include any other information.",
)

Key Concepts in Professional Ethics

**Headings:**
*   Ethics
*   Ethical Behaviour
*   Ethical Reasoning
*   Ethical System
*   Unethical
*   Non-ethical Considerations
*   Ethical Dilemma

**Text:**
*   The process of determining right and wrong conduct. The discipline dealing with what is good and bad and with moral duty and obligations
*   Behaviour that conforms to accepted standards of conduct
*   The process of sorting out the principles that help determine what is ethical when faced with an ethical dilemma
*   A specific formula for distinguishing right from wrong
*   An action or conduct which violates the principles of one or more ethical systems, or which is counter to an accepted ethical value, such as honesty
*   Powerful human motivations that are not based on right or wrong, but on considerations of survival and well-being, such as health, security, love, wealth, or selfesteem
*   This is an ethical problem in which the ethical choice involves ignoring a powerful non-eth

In [42]:
def extract_topic(text):
    """
    Extracts the topic from LLM output.
    Topic assumed to be first non-empty line before the '**Headings:**' section.
    """
    match = re.search(r"^(.*?)\n\s*\*{2}Headings:{2}", text, re.DOTALL | re.MULTILINE)
    if match:
        topic = match.group(1).strip()
        return topic
    # fallback: first non-empty line
    for line in text.splitlines():
        if line.strip():
            return line.strip()
    return None

llm_text = final_result.content  # Your LLM output string

topic = extract_topic(llm_text)
print("Topic:\n", topic)

Topic:
 Key Concepts in Professional Ethics


In [43]:
def extract_headings(text):
    """
    Best and most reliable method to extract headings
    """
    lines = text.split("\n")
    headings = []
    in_headings_section = False

    for line in lines:
        line = line.strip()

        # Start collecting headings after **Headings:**
        if "**Headings:**" in line:
            in_headings_section = True
            continue

        # Stop collecting when **Text:** appears
        if "**Text:**" in line:
            break

        # Collect bullet points in headings section
        if in_headings_section and line.startswith("* "):
            heading = line[2:].strip()  # Remove '* ' and extra spaces
            if heading:
                headings.append(heading)

    return headings


# Usage example:
llm_text = final_result.content
headings = extract_headings(llm_text)

print("\nHeadings:")
for h in headings:
    print("-", h)


Headings:
- Ethics
- Ethical Behaviour
- Ethical Reasoning
- Ethical System
- Unethical
- Non-ethical Considerations
- Ethical Dilemma


In [44]:
def extract_paragraphs(text):
    """
    Best method to extract paragraphs from **Text:** section
    """
    lines = text.split('\n')
    paragraphs = []
    in_text_section = False
    
    for line in lines:
        line = line.strip()
        
        # Start collecting after **Text:**
        if "**Text:**" in line:
            in_text_section = True
            continue
        
        # Stop if another section starts or end of meaningful content
        if in_text_section and line.startswith('**') and line.endswith('**'):
            break
        
        # Stop at PDF saved or similar end markers
        if "PDF saved:" in line or line.startswith('PDF '):
            break
        
        # Collect bullet points in text section
        if in_text_section and line.startswith('* '):
            paragraph = line[2:].strip()  # Remove '* ' and extra spaces
            if paragraph:
                paragraphs.append(paragraph)
    
    return paragraphs

llm_text = final_result.content
paragraphs = extract_paragraphs(llm_text)

print("\nParagraphs:")
for p in paragraphs:
    print("-", p)



Paragraphs:
- The process of determining right and wrong conduct. The discipline dealing with what is good and bad and with moral duty and obligations
- Behaviour that conforms to accepted standards of conduct
- The process of sorting out the principles that help determine what is ethical when faced with an ethical dilemma
- A specific formula for distinguishing right from wrong
- An action or conduct which violates the principles of one or more ethical systems, or which is counter to an accepted ethical value, such as honesty
- Powerful human motivations that are not based on right or wrong, but on considerations of survival and well-being, such as health, security, love, wealth, or selfesteem
- This is an ethical problem in which the ethical choice involves ignoring a powerful non-ethical consideration.


In [45]:
def generate_audio(paragraphs):

    """Generate audio from text using Kokoro pipeline."""
    if not paragraphs or not final_result.content:
        print("No content to generate audio from.")
        return None

        # Initialize Kokoro pipeline
    pipeline = KPipeline(lang_code="a")  # Use appropriate language code
    generator = pipeline(paragraphs, voice="am_onyx", speed=1)

    audio_data = []

    # Step 3: Loop through generated audio chunks
    for i, (gs, ps, audio) in enumerate(generator):
        print(f"Chunk {i}: gs={gs}, ps={ps}")
        display(Audio(data=audio, rate=24000, autoplay=i == 0))
        audio_data.append(audio)

    # Step 4: Process and save audio
    if audio_data:
        # Concatenate all audio chunks
        combined_audio = np.concatenate(audio_data)

        # Normalize to prevent clipping (keep some headroom)
        max_val = np.max(np.abs(combined_audio))
        if max_val > 0:
            combined_audio = combined_audio / max_val * 0.9

        # Save using scipy (automatically handles float32 to int16 conversion)
        Audio_file_name = input("Enter the file name")
        my_audio_file_path = rf"../my_audios/{Audio_file_name}"
        wavfile.write(f"{my_audio_file_path}.wav", 24000, combined_audio)
        print("Audio generated successfully:")

        # Display final combined audio
        display(Audio(f"{my_audio_file_path}.wav"))
    else:
        print("No audio data generated. Check your pipeline/text input.")


generate_audio(paragraphs)

Chunk 0: gs=The process of determining right and wrong conduct. The discipline dealing with what is good and bad and with moral duty and obligations, ps=ðə pɹˈɑsˌɛs ʌv dətˈɜɹmənɪŋ ɹˈIt ænd ɹˈɔŋ kˈɑndˌʌkt. ðə dˈɪsəplən dˈilɪŋ wɪð wˌʌt ɪz ɡˈʊd ænd bˈæd ænd wɪð mˈɔɹᵊl dˈuTi ænd ˌɑbləɡˈAʃənz


Chunk 1: gs=Behaviour that conforms to accepted standards of conduct, ps=bəhˈAvjəɹ ðæt kənfˈɔɹmz tʊ əksˈɛptᵻd stˈændəɹdz ʌv kˈɑndˌʌkt


Chunk 2: gs=The process of sorting out the principles that help determine what is ethical when faced with an ethical dilemma, ps=ðə pɹˈɑsˌɛs ʌv sˈɔɹTɪŋ ˈWt ðə pɹˈɪnsəpᵊlz ðæt hˈɛlp dətˈɜɹmən wˌʌt ɪz ˈɛθəkəl wˌɛn fˈAst wɪð ɐn ˈɛθəkəl dəlˈɛmə


Chunk 3: gs=A specific formula for distinguishing right from wrong, ps=ɐ spəsˈɪfɪk fˈɔɹmjələ fɔɹ dəstˈɪŋɡwɪʃɪŋ ɹˈIt fɹʌm ɹˈɔŋ


Chunk 4: gs=An action or conduct which violates the principles of one or more ethical systems, or which is counter to an accepted ethical value, such as honesty, ps=ɐn ˈækʃən ɔɹ kˈɑndˌʌkt wˌɪʧ vˈIəlˌAts ðə pɹˈɪnsəpᵊlz ʌv wˈʌn ɔɹ mˈɔɹ ˈɛθəkəl sˈɪstəmz, ɔɹ wˌɪʧ ɪz kˈWntəɹ tə ɐn əksˈɛptᵻd ˈɛθəkəl vˈælju, sˈʌʧ æz ˈɑnəsti


Chunk 5: gs=Powerful human motivations that are not based on right or wrong, but on considerations of survival and well-being, such as health, security, love, wealth, or selfesteem, ps=pˈWəɹfᵊl hjˈumən mˌOTəvˈAʃənz ðæt ɑɹ nˌɑt bˈAst ˌɔn ɹˈIt ɔɹ ɹˈɔŋ, bˌʌt ˌɔn kənsˌɪdəɹˈAʃənz ʌv səɹvˈIvᵊl ænd wˈɛlbˌiɪŋ, sˈʌʧ æz hˈɛlθ, səkjˈʊɹəTi, lˈʌv, wˈɛlθ, ɔɹ sˌɛlfɪstˈim


Chunk 6: gs=This is an ethical problem in which the ethical choice involves ignoring a powerful non-ethical consideration., ps=ðˌɪs ɪz ɐn ˈɛθəkəl pɹˈɑbləm ɪn wˌɪʧ ði ˈɛθəkəl ʧˈYs ɪnvˈɑlvz ɪɡnˈɔɹɪŋ ɐ pˈWəɹfᵊl nˌɑnˈɛθəkəl kənsˌɪdəɹˈAʃən.


Audio generated successfully:


In [47]:
from moviepy.editor import (
    TextClip,
    ColorClip,
    CompositeVideoClip,
    AudioFileClip,
    concatenate_videoclips,
)
from moviepy.config import change_settings

# ImageMagick path
def create_Topic_and_headings_frame_with_audio(
    topic, headings_list, audio_path, output_file="headings_frame_with_audio.mp4"
):
    # Flatten headings list
    flat_headings = []
    for h in headings_list:
        if isinstance(h, (list, tuple)):
            flat_headings.extend(h)
        else:
            flat_headings.append(str(h))

    # Remove topic if present in headings
    clean_headings = [h for h in flat_headings if h.strip() != topic.strip()]

    # Load audio to get duration
    audio_clip = AudioFileClip(audio_path)
    total_duration = audio_clip.duration

    # Calculate timing - NO topic duration, only headings
    num_headings = len(clean_headings)

    if num_headings > 0:
        heading_duration = (
            total_duration / num_headings
        )  # Saara time headings ko divide
    else:
        heading_duration = 2.0

    print(
        f"Total headings: {num_headings}, Each heading duration: {heading_duration:.1f}s"
    )

    video_segments = []
    current_time = 0

    # Each heading highlight segments - Topic sirf title ki tarah rahega
    for i, heading in enumerate(clean_headings):
        # Create text with topic as title and current heading highlighted
        text_lines = [topic.strip(), ""]  # Topic title (no highlighting)

        for j, h in enumerate(clean_headings):
            if j == i:
                text_lines.append(f">> {h.strip()} <<")  # Only heading highlighted
            else:
                text_lines.append(h.strip())

        segment_text = "\n".join(text_lines)
        segment_dur = min(heading_duration, total_duration - current_time)

        if segment_dur <= 0:
            break

        # Create text clip
        text_clip = (
            TextClip(
                segment_text,
                fontsize=30,
                color="white",
                size=(1100, 650),
                method="caption",
                align="west",
                font="Arial",
            )
            .set_position((180, "center"))
            .set_duration(segment_dur)
        )

        # Background and audio
        bg_clip = ColorClip(size=(1280, 720), color=(0, 0, 0)).set_duration(segment_dur)
        segment_audio = audio_clip.subclip(current_time, current_time + segment_dur)
        segment_video = CompositeVideoClip([bg_clip, text_clip]).set_audio(
            segment_audio
        )
        video_segments.append(segment_video)
        current_time += segment_dur

    # Combine all segments
    final_clip = concatenate_videoclips(video_segments)

    # Export video
    final_clip.write_videofile(output_file, fps=24)

    # Cleanup
    audio_clip.close()
    final_clip.close()


# Usage - exactly like before, just replace audio_clip with actual path
path = rf"../Video_lectures"
video_lect = input("Enter the name of the file: ")
audio_file_path = audio_clip  # Replace this with actual path

create_Topic_and_headings_frame_with_audio(
    topic, headings, audio_file_path, f"{path}/{video_lect}.mp4"
)

Total headings: 7, Each heading duration: 7.2s
Moviepy - Building video ../Video_lectures/L13.mp4.
MoviePy - Writing audio in L13TEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video ../Video_lectures/L13.mp4



Moviepy - Done !
Moviepy - video ready ../Video_lectures/L13.mp4
